In [4]:
!pip install -U pandas-profiling
!pip install MarkupSafe==2.0.1
import pandas as pd
from sqlalchemy import create_engine
import os
import pandas_profiling

     |████████████████████████████████| 315 kB 6.1 MB/s eta 0:00:01
     |████████████████████████████████| 694 kB 28.7 MB/s eta 0:00:01
     |████████████████████████████████| 102 kB 53.1 MB/s eta 0:00:01
  Using cached htmlmin-0.1.12-py3-none-any.whl
     |████████████████████████████████| 3.2 MB 5.7 MB/s eta 0:00:01
     |████████████████████████████████| 4.7 MB 32.2 MB/s eta 0:00:01
     |████████████████████████████████| 296 kB 74.7 MB/s eta 0:00:01


In [6]:
df = pd.read_csv("Spotify-2000.csv")

In [7]:
df.head()

Index                   Title             Artist            Top Genre  \
0      1                 Sunrise        Norah Jones      adult standards   
1      2             Black Night        Deep Purple           album rock   
2      3          Clint Eastwood           Gorillaz  alternative hip hop   
3      4           The Pretender       Foo Fighters    alternative metal   
4      5  Waitin' On A Sunny Day  Bruce Springsteen         classic rock   

   Year  Beats Per Minute (BPM)  Energy  Danceability  Loudness (dB)  \
0  2004                     157      30            53            -14   
1  2000                     135      79            50            -11   
2  2001                     168      69            66             -9   
3  2007                     173      96            43             -4   
4  2002                     106      82            58             -5   

   Liveness  Valence Length (Duration)  Acousticness  Speechiness  Popularity  
0        11       68               201            94            3          71  
1        17       81               207            17            7          39  
2         7       52               341             2           17          69  
3         3       37               269             0            4          76  
4        10       87               256             1            3          59

In [8]:
profile=df.profile_report()
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [9]:
df_artist = pd.DataFrame(list(df['Artist'].unique()),columns=['artist_name']).reset_index()
df_artist=df_artist.rename(columns={"index":"artist_id"})
df_artist.head()

artist_id        artist_name
0          0        Norah Jones
1          1        Deep Purple
2          2           Gorillaz
3          3       Foo Fighters
4          4  Bruce Springsteen



- Split DF to different smaller DFs
- Artist
- Genres
- Song info/characteristics (title-artist-length)
- Song characteristics
- Write to SQL DB






# Michael Moore editing Genres


In [10]:
def genre_colaspe(genre_att):
    genres = 'rock metal pop jazz soul blues punk country folk funk\
    rap house dance dutch indie singer-songwriter latin reggae'.split()
    genres.append('hip hop')
    #print(genres)
    for genre in genres:
        if genre in genre_att:
            return genre
    return genre_att
    

In [12]:
df['Top Genre'] = df['Top Genre'].apply(genre_colaspe)


In [ ]:
# end of edit

In [13]:
df_genres = pd.DataFrame(list(df['Top Genre'].unique()),columns=['genre_name']).reset_index()
df_genres=df_genres.rename(columns={"index":"genre_id"})
df_genres

genre_id             genre_name
0          0        adult standards
1          1                   rock
2          2                hip hop
3          3                  metal
4          4                    pop
5          5                  dutch
6          6         permanent wave
7          7                  dance
8          8                   soul
9          9                  disco
10        10               big room
11        11             neo mellow
12        12               boy band
13        13       carnaval limburg
14        14                country
15        15                  latin
16        16                   folk
17        17                 celtic
18        18                chanson
19        19                electro
20        20              downtempo
21        21                 reggae
22        22       british invasion
23        23                   jazz
24        24                 trance
25        25      singer-songwriter
26        26            mellow gold
27        27                  blues
28        28               big beat
29        29                   funk
30        30         happy hardcore
31        31       classic schlager
32        32                  gabba
33        33                    edm
34        34            electronica
35        35                  indie
36        36       stomp and holler
37        37       australian psych
38        38            laboratorio
39        39     classic soundtrack
40        40  compositional ambient
41        41             streektaal
42        42                    ccm
43        43                  house
44        44   australian americana
45        45                 j-core
46        46                   punk
47        47               basshall
48        48            christelijk
49        49             levenslied
50        50                    rap
51        51                 motown
52        52                  bebop

In [16]:
df_songs = pd.DataFrame(df[['Title','Artist','Top Genre','Year']]).reset_index()
df_songs.columns=['song_id','title','artist_name','genre_name','year']
df_songs

song_id                   title               artist_name  \
0           0                 Sunrise               Norah Jones   
1           1             Black Night               Deep Purple   
2           2          Clint Eastwood                  Gorillaz   
3           3           The Pretender              Foo Fighters   
4           4  Waitin' On A Sunny Day         Bruce Springsteen   
...       ...                     ...                       ...   
1989     1989        Heartbreak Hotel             Elvis Presley   
1990     1990               Hound Dog             Elvis Presley   
1991     1991         Johnny B. Goode               Chuck Berry   
1992     1992               Take Five  The Dave Brubeck Quartet   
1993     1993          Blueberry Hill               Fats Domino   

           genre_name  year  
0     adult standards  2004  
1                rock  2000  
2             hip hop  2001  
3               metal  2007  
4                rock  2002  
...               ...   ...  
1989  adult standards  1958  
1990  adult standards  1958  
1991             rock  1959  
1992            bebop  1959  
1993  adult standards  1959  

[1994 rows x 5 columns]

In [17]:
df_songs=df_songs.merge(df_artist).merge(df_genres)
df_songs.drop(['artist_name','genre_name'],axis=1,inplace=True)
df_songs

song_id                                              title  year  \
0           0                                            Sunrise  2004   
1          33                                     Don't Know Why  2002   
2          10                                     Love Me Tender  2002   
3         144  A Little Less Conversation - JXL Radio Edit Remix  2002   
4         387                     (You're The) Devil in Disguise  2002   
...       ...                                                ...   ...   
1989     1789                                     Ik Heb Je Lief  1998   
1990     1535   Lekker Op De Trekker ('n Boerinnen-Wervingslied)  1991   
1991     1589                                        Jump Around  1992   
1992     1880                   It's A Man's, Man's, Man's World  1966   
1993     1992                                          Take Five  1959   

      artist_id  genre_id  
0             0         0  
1             0         0  
2            10         0  
3            10         0  
4            10         0  
...         ...       ...  
1989        604        48  
1990        611        49  
1991        626        50  
1992        706        51  
1993        729        52  

[1994 rows x 5 columns]

In [34]:
df_songs['year'] = pd.to_datetime(df_songs.year, format='%Y').dt.year
df_songs

song_id                                              title  year  \
0           0                                            Sunrise  2004   
1          33                                     Don't Know Why  2002   
2          10                                     Love Me Tender  2002   
3         144  A Little Less Conversation - JXL Radio Edit Remix  2002   
4         387                     (You're The) Devil in Disguise  2002   
...       ...                                                ...   ...   
1989     1789                                     Ik Heb Je Lief  1998   
1990     1535   Lekker Op De Trekker ('n Boerinnen-Wervingslied)  1991   
1991     1589                                        Jump Around  1992   
1992     1880                   It's A Man's, Man's, Man's World  1966   
1993     1992                                          Take Five  1959   

      artist_id  genre_id  
0             0         0  
1             0         0  
2            10         0  
3            10         0  
4            10         0  
...         ...       ...  
1989        604        48  
1990        611        49  
1991        626        50  
1992        706        51  
1993        729        52  

[1994 rows x 5 columns]

In [18]:
df_song_characteristics = pd.DataFrame(df[['Beats Per Minute (BPM)','Energy','Danceability','Loudness (dB)','Liveness','Valence','Length (Duration)','Acousticness','Speechiness','Popularity']]).reset_index()
new_labels = ['song_id','bpm','energy','danceability','db','liveness','valence','length','acousticness','speechiness','popularity']
df_song_characteristics.columns=new_labels
df_song_characteristics

song_id  bpm  energy  danceability  db  liveness  valence length  \
0           0  157      30            53 -14        11       68    201   
1           1  135      79            50 -11        17       81    207   
2           2  168      69            66  -9         7       52    341   
3           3  173      96            43  -4         3       37    269   
4           4  106      82            58  -5        10       87    256   
...       ...  ...     ...           ...  ..       ...      ...    ...   
1989     1989   94      21            70 -12        11       72    128   
1990     1990  175      76            36  -8        76       95    136   
1991     1991  168      80            53  -9        31       97    162   
1992     1992  174      26            45 -13         7       60    324   
1993     1993  133      50            49 -10        16       83    148   

      acousticness  speechiness  popularity  
0               94            3          71  
1               17            7          39  
2                2           17          69  
3                0            4          76  
4                1            3          59  
...            ...          ...         ...  
1989            84            7          63  
1990            73            6          69  
1991            74            7          74  
1992            54            4          65  
1993            74            3          56  

[1994 rows x 11 columns]

In [19]:
df_songs.head(1)

song_id    title  year  artist_id  genre_id
0        0  Sunrise  2004          0         0

In [20]:
df_artist.head(1)

artist_id  artist_name
0          0  Norah Jones

In [21]:
df_genres.head(1)

genre_id       genre_name
0         0  adult standards

In [22]:
df_song_characteristics.head(1)

song_id  bpm  energy  danceability  db  liveness  valence length  \
0        0  157      30            53 -14        11       68    201   

   acousticness  speechiness  popularity  
0            94            3          71

In [23]:
df_songs.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1994 entries, 0 to 1993
Data columns (total 5 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   song_id    1994 non-null   int64 
 1   title      1994 non-null   object
 2   year       1994 non-null   int64 
 3   artist_id  1994 non-null   int64 
 4   genre_id   1994 non-null   int64 
dtypes: int64(4), object(1)
memory usage: 93.5+ KB


In [24]:
!pip install mysql.connector
!pip install sqlalchemy

     |████████████████████████████████| 11.9 MB 3.4 MB/s eta 0:00:01
  Created wheel for mysql.connector: filename=mysql_connector-2.2.9-cp39-cp39-macosx_10_9_x86_64.whl size=247972 sha256=9dcc4805a11d1b00c0e34a3dd0ffdffd8fd30943d233f9d700e30228ffa7f751
  Stored in directory: /Users/mikemoore26/Library/Caches/pip/wheels/7b/14/39/5aad423666e827dfe9a1fbcd111ac17171e7c9865d570780ce
Successfully built mysql.connector


In [25]:
# from google.colab import drive
# drive.mount('/content/drive')

ModuleNotFoundError: No module named 'google.colab'

In [ ]:
import mysql.connector
import sqlite3
from sqlalchemy import create_engine
db_path = "sqlite:////content/drive/MyDrive/spotify-2000/data.db"
# csv_path = "/content/sample_data/Spotify-2000.csv"
engine = create_engine(db_path)


In [ ]:
df_songs.to_sql(name="songs",con=engine, if_exists="replace",index=False)

In [ ]:
df_song_characteristics.to_sql(name="characteristics",con=engine, if_exists="replace",index=False)
df_artist.to_sql(name="artist",con=engine, if_exists="replace",index=False)
df_genres.to_sql(name="genres",con=engine, if_exists="replace",index=False)

In [ ]:
r_set=engine.execute('''SELECT * from songs''');
for row in r_set:
    print(row)

In [ ]:
r_set=engine.execute('''SELECT * from artist''');
for row in r_set:
    print(row)


In [ ]:
r_set=engine.execute('''SELECT * from genres''');
for row in r_set:
    print(row)

In [ ]:
r_set=engine.execute('''SELECT * from characteristics''');
for row in r_set:
    print(row)

In [35]:
df_songs.to_csv('./df_songs2.csv',index=False)
df_genres.to_csv('./df_genres2.csv',index=False)


In [26]:
df_songs.to_csv('/content/drive/MyDrive/spotify-2000/df_songs2.csv',index=False)
df_song_characteristics.to_csv('/content/drive/MyDrive/spotify-2000/df_characteristics.csv',index=False)
df_genres.to_csv('/content/drive/MyDrive/spotify-2000/df_genres2.csv',index=False)
df_artist.to_csv('/content/drive/MyDrive/spotify-2000/df_artists.csv',index=False)

OSError: Cannot save file into a non-existent directory: '/content/drive/MyDrive/spotify-2000'